# PySyft: Data Science on data you are not allowed to see

Getting access to **data** is the first, and yet the most crucial step in **Data Science** - but often getting access to _enough_ data is impossible. 

Ideally, all that would be necessary for a data scientist is to _connect_ to the web server where the data is stored, so they can get started with their analyses. 
Unfortunately though, it is not _that_ simple! 
Public access to information always comes with several risks, and necessarily leads to concerns about trust (e.g. _data copy/use/misuse_), privacy (e.g. _disclosure of senstive information_), or legal implications (e.g. _moving data outside their original silos_).

But, what if we'd tell you that actually, it **can** be _that_ simple ?! 

```{epigraph}
A _new way_ to do data science, where you can use non-public information, without seeing nor obtaining a copy of the data itself. All you need is to connect to a **Datasite**, and use PySyft! 
```

In this tutorial, we will learn the **four** simple steps that are necessary to use PySyft, and to run your code on data _you are not allowed to see_.

## 1. Login to the Datasite

In this beginning of your journey with PySyft, there is one key term to remember: [**Datasite**](./components/datasets.ipynb).

```{epigraph} 
Think of a Datasite as a website, but for data. While web servers allow you to download files like `.html` or `.css` to your browser, Datasites operate differently. 

A Datasite enables a data scientist to retrieve *answers* to their research questions from the data, *without actually downloading nor seeing* the data.
```

Let's use togheter our first *PySyft Datasite* and explore what questions we can answer with the data it hosts!

```{warning}

We will assume you have <b>PySyft installed</b>. Please refer to the [Quick install PySyft](./quick-install.ipynb) for further information.
```

Let's first login into the Datasite using `syft`:

In [1]:
import syft as sy

# login to data_site
client = sy.login_as_guest(url="20.51.219.43:80")

Logged into <university-wisconsin: High-side Datasite> as GUEST


## 2. Discover the data on the Datasite

Now that we are logged in (_as guests_, ed.) into the Datasite, let's explore what data is available. We do so by accessing [`client.datasets`](./components/datasets.ipynb):

In [2]:
client.datasets

The `pysyft-demo-datasite` server is hosting **one** dataset, named "Breast Cancer Wisconsin". We can use PySyft APIs to get a _pointer_ to the remote dataset:

In [3]:
breast_cancer_dataset = client.datasets["Breast Cancer Wisconsin"]

As this is our first interaction with the "Breast Cancer Wisconsin" dataset, let's get additional information to better understand what this data is about. We can do so by simpy accessing the _rich_ preview from our `breast_cancer_dataset` remote pointer:

In [4]:
breast_cancer_dataset

syft.service.dataset.dataset.Dataset

As you can see, the dataset preview includes:
- a **summary**: brief description of the dataset.
- a **description** with further information about what data is included, its intended use, and characteristics of the data (_so we know what we should expect_, ed.).
- The list of the **two assets**, i.e. "BC Features", and "BC Targets", storing the data.

<div class="alert alert-info">
    💡 <b>Take away</b>: We just learnt that a PySyft <b>dataset</b> is the union of <b>metadata</b> information, useful to get a a general understaning about the data, and <b>assets</b>. 
</div>

Similarly to what we did with the dataset, we can get a pointer to each of the remote assets in `breast_cancer_dataset`:

In [5]:
features, targets = breast_cancer_dataset.assets

**However**, if we would try to access the `data` from these assets:

In [6]:
features.data

SyftError: You do not have permission to access private data.

<div class="alert alert-danger">
    ✋ <b>We do not have permissions to access the data!</b> 🛑
</div>

This is indeed one of the main features of PySyft: as `GUEST` Data Scientists to the Datasite, we are **not allowed** to see nor download any data from the dataset! 

_At this point, you may wonder_: 

> How could I possibly work with data I cannot see? How could I even start to work on my code, if that cannot be tested with data ?

PySyft addresses this issue by hosting **two types** of data in each [**asset**](./components/datasets.ipynb#create-an-asset): _real_ data (e.g. `features.data`) and _mock_ data (e.g. `features.mock`).

**Mock** data represents an artificial version of the true data, that has been made available through PySyft for code preparation purposes. Let's have a quick look:

In [7]:
features.mock.head(n=3)

Unnamed: 0    radius1   texture1  perimeter1        area1  smoothness1  \
0  284.236697  32.790832  30.322750  215.075411  1655.906854     0.835428   
1  285.419316  35.387568  37.773586  225.360959  1980.940592     0.914992   
2  286.557667  34.480210  41.535379  222.280991  1858.304816     1.086516   

   compactness1  concavity1  concave_points1  symmetry1  ...    radius3  \
0      1.069219    0.504109         0.839460   0.752551  ...  42.127052   
1      0.883861    0.825926         0.823268   1.267871  ...  41.328957   
2      0.755101    0.674030         0.636585   0.628226  ...  40.519997   

    texture3  perimeter3        area3  smoothness3  compactness3  concavity3  \
0  43.919680  292.127453  2900.460981     1.114412      1.724469    1.865109   
1  49.758043  267.028592  2837.115333     1.248279      0.964296    1.393830   
2  51.879152  259.949887  2590.176379     0.667455      0.862762    1.238147   

   concave_points3  symmetry3  fractal_dimension3  
0         0.859462   1.405402            0.923620  
1         1.151001   1.478893            0.985656  
2         1.049442   1.500712            0.852664  

[3 rows x 31 columns]

In [8]:
targets.mock.sample(n=3, random_state=24)

Unnamed: 0 Diagnosis
338         248         B
488         236         M
345         104         B

## 3. Prepare the code to answer our Research Question

The presence of `mock` data provides a concrete strategy to work on our code, and more importantly, to concentrate on what _really matters_: our **research question**. 

Let's say we are interested in knowing what is the difference (on _average_) of the `radius` of the nuclei of the breast tumors for patients with a benign (`B`) or a malign (`M`) diagnoses. 

We can _translate_ this question into Python code that can actually runs, using mock data as **proxy** for the real one:

In [9]:
def average_radius_of_nuclei(data, labels) -> tuple[float, float]:
    """Calculate the mean of `radius` feature, for both samples with bening and malign diagnosis"""
    
    y = labels['Diagnosis'].values.ravel()
    mean_bening = data[y == "B"]["radius3"].mean() 
    mean_malign = data[y == "M"]["radius3"].mean()
    return mean_bening, mean_malign


Let's test our code on mock data:

In [10]:
average_radius_of_nuclei(features.mock, targets.mock)

(33.18213776377855, 32.763550736274205)

It works! ✅ 

We have just verified that our code would be able to work on the selected assets, and so it is ready to for execution on the Datasite.

```{warning} Obtaining the real answer
It is important to emphasise that <em>that</em> result (and <em>any other result</em>, ed.) generated using <b>mock</b> data is completely <b>meaningless</b> for our research question!
We need to run our code on the <em>real</em> (remote) data on the Datasite to get the answer we are looking for. And we will use PySyft for it! 
```

## 4. Get the _true_ answer to our Research Question

Now that we have checked that our code runs _locally_ on _mock_ data, we are now ready to proceed with the last step. 
This time, we want our code to be executed _remotely_ (on the Datasite), and using the _real_ non-public data. We just need to convert our (local) Python function, into a [**remote code request**](./components/requests-api.ipynb#create-a-code-request). 

Creating a code request in PySyft is very easy as it only requires a Python decorator to wrap our 
function with: [`syft.syft_function_single_use`](./components/code-api.ipynb#what-is-a-syft-function). Using this decorator, we will need to specify which assets we are willing to use for our execution (i.e. `features` and `targets` in our case). In this way, we can clearly delimit the _data_ scope of our experiment, as PySyft will **not** allow our execution on [assets different that the ones specified](./components/syft-policies.ipynb#input-output-policies).

In [11]:
@sy.syft_function_single_use(data=features, labels=targets)  # mapping parameters to corresponding assets
def average_radius_of_nuclei(data, labels) -> tuple[float, float]:
    """Calculate the mean of `radius` feature, for both samples with bening and malign diagnosis"""
    
    y = labels['Diagnosis'].values.ravel()
    mean_bening = data[y == "B"]["radius3"].mean() 
    mean_malign = data[y == "M"]["radius3"].mean()
    return mean_bening, mean_malign

SyftSuccess: Syft function 'average_radius_of_nuclei' successfully created. To add a code request, please create a project using `project = syft.Project(...)`, then use command `project.create_code_request`.

**Success**! 🎉 

Now our `average_radius_of_nuclei` function has officially become a PySyft code request, that we can immediately submit to the Datasite:

In [12]:
client.code.request_code_execution(average_radius_of_nuclei)

syft.service.request.request.Request

```{warning} Waiting for approval
Please wait one second before proceed to make sure that the demo servers will receive and automatically approves the requests.
```

Let's check the _status_ of our request:

In [13]:
client.code

The request has been **automatically approved** by the Datasite! This means we have now permission to _remotely_ execute our code on the _real_ data, and then download the answer:

In [15]:
answer = client.code.average_radius_of_nuclei(data=features, labels=targets)
print(answer)

(13.37980112044818, 21.134811320754718)


Well done!! 👏 

You have successfully executed the `average_radius_of_nuclei` function _remotely_ on the Datasite, and obtained the results from the _real_ (non-public) data! And all, without ever looking at the data!

## This is just the surface 🔎

Congratulations for completing your first **PySyft** tutorial!  In this tutorial, we have learnt how easy is to get started with PySyft to allow data science on data _you are not allowed to see_.


**But this was just the surface!**

```{admonition} Approval flow
<em>For example</em>: the demo Datasite server that was used in the tutorial has been configured to <b>automatically accept</b> every single incoming request. In practice, this means that there is <em>no</em> limitation imposed on the <em>queries</em> an external data scientist could submit on the data, with their code 

Naturally, this was just an over-simplification, created solely to make this tutorial as more accessible as possible! But there is <b>so much more</b> to unveil about PySyft features!!
```

If you wish to discover more about PySyft, and learn how to use PySyft _from the ground up_, read this [tutorial](./getting-started/introduction.ipynb). 

You can also [join](https://bit.ly/join-om-slack) the community on Open Mined Slack, and message the `#support` channel where someone will gladly assist you! 

Thanks for your interest!

<!-- ```{eval-rst}

<h4>Learn more about PySyft</h4>
<br>

.. grid:: 1 2 3 3
:gutter: 2

.. grid-item-card::

    Getting Started
    ^^^

    +++

    .. button-ref:: getting_started/introduction
        :expand:
        :color: secondary
        :click-parent:

        Learn more

.. grid-item-card::

    Deployment
    ^^^

    - `Deployment Guide <notebooks/deployment/deployment-doc-1-2-intro-req.html>`_
    - `Beginner-friendly deployment <notebooks/deployment/deployment-doc-4_0-container-based-deployment.html>`_
    - `Orchestrated Deployment <notebooks/deployment/deployment-doc-5_0-deploy-k8s.html>`_
    - `Troubleshooting <notebooks/deployment/deployment-doc-6-troubleshooting.html>`_
    +++

    .. button-ref:: notebooks/deployment/deployment-doc-1-2-intro-req
        :expand:
        :color: secondary
        :click-parent:

        Learn more

.. grid-item-card::

    Components
    ^^^

    - `Datasite Server <notebooks/components/datasite-server.html>`_
    - `Datasets in PySyft <notebooks/components/datasets.html>`_
    - `Policies & privacy in PySyft <notebooks/components/syft-policies.html>`_

    +++

    .. button-ref:: notebooks/components/datasite-server
        :expand:
        :color: secondary
        :click-parent:

        Learn more
``` -->